In [1]:
# Code to allow GPU access
import tensorflow.compat.v1 as tf 
tf.enable_eager_execution(tf.ConfigProto(log_device_placement=True)) 
tf.test.gpu_device_name()

'/device:DML:0'

In [2]:
'''LOADING DATA FROM FILES'''

import pandas as pd
import os

# Load label file
label_df = pd.read_excel('../Data/wax/data labels anna - simple.xlsx')
# clean up column names
label_df.columns = ['code', 'month', 'ID', 'optimality', 'abnormal', 'AIMS']
print(label_df.head())

# Cleanup data, remove rows where AIMS score is 999
#cleaned_label_df = label_df[label_df.AIMS != 999]


   code  month   ID  optimality  abnormal  AIMS
0  1023      0  180           9       1.0     1
1  1023      1  195          14       1.0   999
2  1023      2  197          26       1.0     1
3  1023      3  206          11       1.0     2
4  1023      4  208          13       1.0     1


In [3]:
'''LOADING SENSOR DATA INTO DATAFRAMES and TRIMMING TRIALS'''

import matplotlib.pyplot as plt
import numpy as np
import sys

def load_sensor_data(trial_folder, sensor):
    df = pd.read_csv(trial_folder + "/" + sensor + ".csv")
    df = df[(df.T != 0).any()]
    return df

'''def truncate_df(df, min_rows):
    return df[:min_rows]'''

def combine_dfs(dfs):
    return pd.concat(dfs, axis=1)

def process_df(df, min_rows):
    # Drop rows where all entries are zero
    df = df[(df.T != 0).any()]
    # Truncate dataframe to min_rows
    df = df[:min_rows]
    return df

def rename_columns(df):
    df.columns = ['Time', 'AccXRA', 'AccYRA', 'AccZRA', 'GyrXRA', 'GyrYRA', 'GyrZRA', 'MagXRA', 'MagYRA', 'MagZRA',
                  'AccXLA', 'AccYLA', 'AccZLA', 'GyrXLA', 'GyrYLA', 'GyrZLA', 'MagXLA', 'MagYLA', 'MagZLA',
                  'AccXRW', 'AccYRW', 'AccZRW', 'GyrXRW', 'GyrYRW', 'GyrZRW', 'MagXRW', 'MagYRW', 'MagZRW',
                  'AccXLW', 'AccYLW', 'AccZLW', 'GyrXLW', 'GyrYLW', 'GyrZLW', 'MagXLW', 'MagYLW', 'MagZLW']
    return df

def renames_columns_sum(df):
    df.columns = ['Time', 'AccXRA', 'AccYRA', 'AccZRA', 'AccSumRA', 'GyrXRA', 'GyrYRA', 'GyrZRA', 'MagXRA', 'MagYRA', 'MagZRA',
                  'AccXLA', 'AccYLA', 'AccZLA', 'AccSumLA', 'GyrXLA', 'GyrYLA', 'GyrZLA', 'MagXLA', 'MagYLA', 'MagZLA',
                  'AccXRW', 'AccYRW', 'AccZRW', 'AccSumRW', 'GyrXRW', 'GyrYRW', 'GyrZRW', 'MagXRW', 'MagYRW', 'MagZRW',
                  'AccXLW', 'AccYLW', 'AccZLW', 'AccSumLW', 'GyrXLW', 'GyrYLW', 'GyrZLW', 'MagXLW', 'MagYLW', 'MagZLW']
    return df

def calculate_acceleration_sums(df):
    df['AccSumRA'] = np.sqrt(df['AccXRA']**2 + df['AccYRA']**2 + df['AccZRA']**2)
    df['AccSumLA'] = np.sqrt(df['AccXLA']**2 + df['AccYLA']**2 + df['AccZLA']**2)
    df['AccSumRW'] = np.sqrt(df['AccXRW']**2 + df['AccYRW']**2 + df['AccZRW']**2)
    df['AccSumLW'] = np.sqrt(df['AccXLW']**2 + df['AccYLW']**2 + df['AccZLW']**2)
    return df

def calculate_rolling_mean(df, window_size):
    df['AccSumSumR_Rolling10000'] = df['AccSumSumR'].rolling(window_size).mean()
    return df

def trim_df(df, start_index, end_index):
    return df.iloc[start_index:end_index-10000]

def drop_columns(df, columns):
    df.drop(columns=columns, inplace=True)
    return df

def calculate_peak_indices(first_half, second_half, column_name):
    start_peak_index = first_half[column_name].idxmax() + 10000
    end_peak_index = second_half[column_name].idxmax() - 10000
    return start_peak_index, end_peak_index

def process_trial(index, row, label_df):

    print("processing instance", index)

    trial_id = row["ID"]
    infant_id = row["code"]

    if trial_id < 10:
        addedZero = '00'
    elif row['ID'] < 100:
        addedZero = '0'
    else:
        addedZero = ''

    trial_folder = '../Data/wax/p' + addedZero + str(trial_id)

    ra_df = load_sensor_data(trial_folder, "RA")
    la_df = load_sensor_data(trial_folder, "LA")
    rw_df = load_sensor_data(trial_folder, "RW")
    lw_df = load_sensor_data(trial_folder, "LW")

    # Get the minimum number of rows across all dataframes
    min_rows = min(ra_df.shape[0], la_df.shape[0], rw_df.shape[0], lw_df.shape[0])  

    #Process each dataframe
    ra_df = process_df(ra_df, min_rows)
    la_df = process_df(la_df, min_rows)
    rw_df = process_df(rw_df, min_rows)
    lw_df = process_df(lw_df, min_rows)

    # Remove first column from la, rw, lw dfs using indexing
    la_df = la_df.iloc[:, 1:]
    rw_df = rw_df.iloc[:, 1:]
    lw_df = lw_df.iloc[:, 1:]

    combined_df = combine_dfs([ra_df, la_df, rw_df, lw_df])
    # find number of columns in combined_df
    num_cols = combined_df.shape[1]

    # If number of columns is 37, acc, gyr and mag data is present.
    # If number of columns is 13, only acc data is present.
    if num_cols == 37:
        combined_df = rename_columns(combined_df)
        combined_df = calculate_acceleration_sums(combined_df)
        allSensors = True
    else:
        combined_df.columns = ['Time', 'AccXRA', 'AccYRA', 'AccZRA', 'AccXLA', 'AccYLA', 'AccZLA', 'AccXRW', 'AccYRW', 'AccZRW', 'AccXLW', 'AccYLW', 'AccZLW']
        combined_df = calculate_acceleration_sums(combined_df)
        allSensors = False


    #combined_df = rename_columns(combined_df)
    #combined_df = calculate_acceleration_sums(combined_df)

    # Split df in half
    first_half = combined_df.iloc[0:combined_df.shape[0]//2]
    second_half = combined_df.iloc[combined_df.shape[0]//2:combined_df.shape[0]]
   
    ra_start_peak_index, ra_end_peak_index = calculate_peak_indices(first_half, second_half, 'AccSumRA')
    la_start_peak_index, la_end_peak_index = calculate_peak_indices(first_half, second_half, 'AccSumLA')
    rw_start_peak_index, rw_end_peak_index = calculate_peak_indices(first_half, second_half, 'AccSumRW')
    lw_start_peak_index, lw_end_peak_index = calculate_peak_indices(first_half, second_half, 'AccSumLW')

    starts = [ra_start_peak_index, la_start_peak_index, rw_start_peak_index, lw_start_peak_index]
    ends = [ra_end_peak_index, la_end_peak_index, rw_end_peak_index, lw_end_peak_index]

    max_end = max(ends)
    max_index = ends.index(max_end)
    max_start = starts[max_index]
    difference = max_end - max_start

    ra_df_trimmed = trim_df(ra_df, ra_start_peak_index, ra_start_peak_index + difference)
    la_df_trimmed = trim_df(la_df, la_start_peak_index, la_start_peak_index + difference)
    rw_df_trimmed = trim_df(rw_df, rw_start_peak_index, rw_start_peak_index + difference)
    lw_df_trimmed = trim_df(lw_df, lw_start_peak_index, lw_start_peak_index + difference) 
    
    # Reset the index of each df
    ra_df_trimmed = ra_df_trimmed.reset_index(drop=True)
    la_df_trimmed = la_df_trimmed.reset_index(drop=True)
    rw_df_trimmed = rw_df_trimmed.reset_index(drop=True)
    lw_df_trimmed = lw_df_trimmed.reset_index(drop=True)


    trimmed_df = combine_dfs([ra_df_trimmed, la_df_trimmed, rw_df_trimmed, lw_df_trimmed])
    num_cols = trimmed_df.shape[1]

    if num_cols == 37:
        trimmed_df = rename_columns(trimmed_df)
        trimmed_df = calculate_acceleration_sums(trimmed_df)
    else:
        trimmed_df.columns = ['Time', 'AccXRA', 'AccYRA', 'AccZRA', 'AccXLA', 'AccYLA', 'AccZLA', 'AccXRW', 'AccYRW', 'AccZRW', 'AccXLW', 'AccYLW', 'AccZLW']
        trimmed_df = calculate_acceleration_sums(trimmed_df)

    # Plot trimmed_df for every 10 instances (sanity check)
    if index % 50 == 0:
        trimmed_df.plot(x='Time', y=['AccSumRA', 'AccSumLA', 'AccSumRW', 'AccSumLW'], title='Sum of Accelerometer Values for each limb (Data trimmed)')    


    # If trimmed_df is empty, raise an exception. Prevents empty dataframes from being added to the list
    if trimmed_df.empty:
        raise Exception("Empty dataframe")

    return trimmed_df, row['month'], row['code'], row['abnormal'], row['AIMS'], row['optimality'], allSensors

sensorX = [] # List of dataframes (just the sensor data)
accelX = [] # List of dataframes (just the accelerometer data)
combinedX = [] # Sensor data, infant ID, infant age
abnormalY = [] # Abnormal / Normal for all sensor data
accelAbnormalY = [] # Abnormal / Normal for just accelerometer data
aimsY = [] # AIMS score
accelAimsY = [] # AIMS score for just accelerometer data
optimalityY = [] # Optimality score
accelOptimalityY = [] # Optimality score for just accelerometer data

combinedX_m = {} # Sensor data, infant ID, infant age, grouped by month
accelX_m = {} # Just the accelerometer data, grouped by month
abnormalY_m = {} # Abnormal / Normal, grouped by month

# Keep track of rows that raise exceptions
error_rows = []

for index, row in label_df.iterrows():
    try:
        combined_df_trimmed, month, code, abnormal, aims, optimality, allSensors = process_trial(index, row, label_df)

        if allSensors:

            # Add all sensor data to sensorX
            sensorX.append(combined_df_trimmed)

            # Add all sensor data, infant ID, infant age to combinedX
            combinedX.append([combined_df_trimmed, month, code])

            # Add just accelerometer data to accelX
            combined_df_trimmed_copy = combined_df_trimmed.copy()
            combined_df_trimmed_copy = drop_columns(combined_df_trimmed_copy, ['MagXRA', 'MagYRA', 'MagZRA', 
                                                                            'MagXLA', 'MagYLA', 'MagZLA', 
                                                                            'MagXRW', 'MagYRW', 'MagZRW', 
                                                                            'MagXLW', 'MagYLW', 'MagZLW']) # drop magnetometer data
            combined_df_trimmed_copy = drop_columns(combined_df_trimmed_copy, ['GyrXRA', 'GyrYRA', 'GyrZRA', 
                                                                            'GyrXLA', 'GyrYLA', 'GyrZLA', 
                                                                            'GyrXRW', 'GyrYRW', 'GyrZRW', 
                                                                            'GyrXLW', 'GyrYLW', 'GyrZLW']) # drop gyroscope data    
            accelX.append(combined_df_trimmed_copy)            
        
            # Add abnormality label to abnormalY
            abnormalY.append(abnormal)

            # Add AIMS score to aimsY
            aimsY.append(aims)

            # Add optimality score to optimalityY
            optimalityY.append(optimality)
        
        else:

            # Add accelerometer data to accelX
            accelX.append(combined_df_trimmed)
            combined_df_copy = combined_df_trimmed.copy()

        # Add abnormality label to accelAbnormalY
        accelAbnormalY.append(abnormal)

        # Add AIMS score to accelAimsY
        accelAimsY.append(aims)

        # Add optimality score to accelOptimalityY
        accelOptimalityY.append(optimality)

        # Add to month in accelXmonths
        if month not in combinedX_m:
            combinedX_m[month] = [combined_df_trimmed_copy, code]
            accelX_m[month] = [combined_df_trimmed_copy]
            abnormalY_m[month] = [abnormal]

        else:
            combinedX_m[month].append([combined_df_trimmed_copy, code])
            accelX_m[month].append(combined_df_trimmed_copy)
            abnormalY_m[month].append(abnormal)

    except FileNotFoundError:
        print("File not found for instance", index)
        error_rows.append((index, row))

    except Exception as e:
        print("Error processing instance", index)
        print("Error", e) 
        # print line number of error
        print("Error on line {}".format(sys.exc_info()[-1].tb_lineno))
        # print line further back in the traceback
        print("Error on line {}".format(sys.exc_info()[-1].tb_next.tb_lineno))
        error_rows.append((index, row))  

# Sanity check: Print results
print("Sensor X:")
print(sensorX[0])
print("Combined X:")
print(combinedX[0])
print("Accel X:")
print(accelX[0])
print("Labels")
print(abnormalY)
print(aimsY)
print(optimalityY)

print("number of accelerometer dataframes:", len(accelX))

processing instance 0
File not found for instance 0
processing instance 1
processing instance 2
File not found for instance 2
processing instance 3
File not found for instance 3
processing instance 4
File not found for instance 4
processing instance 5
File not found for instance 5
processing instance 6
File not found for instance 6
processing instance 7
processing instance 8
processing instance 9
processing instance 10
processing instance 11
File not found for instance 11
processing instance 12
processing instance 13
processing instance 14
Error processing instance 14
Error Empty dataframe
Error on line 185
Error on line 162
processing instance 15
processing instance 16
processing instance 17
File not found for instance 17
processing instance 18
File not found for instance 18
processing instance 19
processing instance 20
processing instance 21
processing instance 22
File not found for instance 22
processing instance 23
File not found for instance 23
processing instance 24
processing in

In [ ]:
# Check that all dataframes in accelX have the same columns
accelX_columns = accelX[0].columns
for df in accelX:
    if not df.columns.equals(accelX_columns):
        print("Dataframes in accelX do not have the same columns")
        break

In [ ]:
# There are 147 trials. I want to extend the number of trials to 161 by splitting the longest trials into two
# Find top 14 dataframes with most rows in accelX
accelX_rows = [df.shape[0] for df in accelX]
sorted_indices = np.argsort(accelX_rows)

# Get the indices of the top 14 dataframes
top_14_indices = sorted_indices[-14:]

# Get the top 14 dataframes
top_14_dataframes = [accelX[i] for i in top_14_indices]

# Get the top 14 labels
top_14_labels = [accelAbnormalY[i] for i in top_14_indices]

# Remove the dataframes from x and y
for i in sorted(top_14_indices, reverse=True):
    del accelX[i]
    del accelAbnormalY[i]

# Split the top 14 dataframes into two
for i in range(len(top_14_dataframes)):

    df = top_14_dataframes[i]
    label = top_14_labels[i]
    
    first_half = df.iloc[0:df.shape[0]//2]
    second_half = df.iloc[df.shape[0]//2:df.shape[0]]
    accelX.append(first_half)
    accelX.append(second_half)

    # Add the labels to accelAbnormalY
    accelAbnormalY.append(label)
    accelAbnormalY.append(label)

# Sanity check: Print results
print("number of accelerometer dataframes:", len(accelX))
print("number of accelerometer labels:", len(accelAbnormalY))



number of accelerometer dataframes: 161
number of accelerometer labels: 161


In [ ]:
# Segment X into windows of 100 samples, non-overlapping. Ensure that accelX is still in a form that it can be used with a CNN
def segment_data(data, window_size):
    segments = []
    for i in range(0, len(data) - window_size, window_size):
        segment = data[i:i+window_size]
        segments.append(segment)
    return segments


# Segment the data
window_size = 100
segmented_accelX = []
for df in accelX:
    segmented_df = segment_data(df, window_size)
    segmented_accelX.append(segmented_df)

# Sanity check: Print results
print("Segmented Accel X:")
print(segmented_accelX[0])

Segmented Accel X:
[      Time   AccXRA   AccYRA   AccZRA   AccXLA   AccYLA   AccZLA   AccXRW  \
0   231.57  0.07910  0.02148 -0.98242  0.07031  0.49902 -0.85840 -0.89062   
1   231.58  0.08691  0.02344 -0.98828  0.07031  0.50391 -0.86035 -0.90430   
2   231.59  0.08691  0.02344 -0.97949  0.07129  0.50488 -0.86133 -0.91797   
3   231.60  0.08398  0.02637 -0.99023  0.07129  0.50488 -0.86133 -0.91797   
4   231.61  0.07324  0.02637 -0.96387  0.06738  0.50488 -0.86133 -0.89355   
..     ...      ...      ...      ...      ...      ...      ...      ...   
95  232.52  0.01465  0.92871  0.50391  0.06836  0.50000 -0.86035 -0.55371   
96  232.53  0.00977  0.88867  0.50391  0.07031  0.50293 -0.86133 -0.51562   
97  232.54 -0.08008  0.88672  0.28516  0.07227  0.50293 -0.85742 -0.50098   
98  232.55 -0.08008  0.87500  0.10644  0.07227  0.50293 -0.86230 -0.50098   
99  232.56 -0.06152  0.84863 -0.18164  0.07031  0.50195 -0.86230 -0.51367   

     AccYRW   AccZRW   AccXLW   AccYLW   AccZLW  AccSum

In [ ]:
"""Type of segmented_accelX: <class 'list'>
Type of segmented_accelX[0]: <class 'list'>
Length of segmented_accelX: 147
Length of segmented_accelX[0]: 590"""

# Conduct PCA dimension reduction to project each window of raw signals into a low dimensional feature space for further processing.
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

# Iterate through each window in segmented_accelX and apply PCA
pca = PCA(n_components=3)
standard_scaler = StandardScaler()
pca_accelX = []

for trial in segmented_accelX:
    pca_trial = []
    for window in trial:
        # replace NaN values with 0
        window = window.fillna(0)
        standardised_window = standard_scaler.fit_transform(window)
        pca_window = pca.fit_transform(standardised_window)
        pca_trial.append(pca_window)
    pca_accelX.append(pca_trial)

# Sanity check: Print results
print("PCA Accel X:")
print(pca_accelX[0])

PCA Accel X:
[array([[-2.57518696e+00,  1.72193745e+00,  2.82750500e+00],
       [-2.66722677e+00,  1.05194361e-01,  1.28980443e+00],
       [-2.71249688e+00, -3.08764808e-01,  6.48175599e-01],
       [-2.95108027e+00, -3.27538705e-01,  4.44593782e-01],
       [-2.92812858e+00, -5.47929900e-01, -3.08651242e-01],
       [-2.71654400e+00, -2.69985392e-02,  2.02376999e-02],
       [-2.62378480e+00, -6.73560251e-02,  1.45242626e-01],
       [-2.45506205e+00, -6.07135167e-01, -7.77094543e-01],
       [-2.41988940e+00,  4.65226699e-02, -9.51759989e-01],
       [-2.22108087e+00,  3.06813203e-01, -2.89814094e-01],
       [-2.06057043e+00,  8.17440907e-01,  2.76986648e-01],
       [-2.01501913e+00,  3.41369125e-01,  1.33431820e-01],
       [-2.12185069e+00,  4.66945217e-01,  8.68772268e-01],
       [-2.11719010e+00, -3.46709947e-02,  9.41870913e-01],
       [-1.97724335e+00, -1.41723346e-01,  4.52668242e-01],
       [-1.79073176e+00, -3.26767153e-02,  7.68106510e-01],
       [-1.70317851e+00,  

In [ ]:
# print shape of data
print("Shape of PCA Accel X:")
print(np.array(pca_accelX).shape)

print("Shape of PCA Accel X [0]:")
print(len(pca_accelX[0]))

print("Shape of PCA Accel X [0][0]:")
print(pca_accelX[0][0].shape)

Shape of PCA Accel X:
(161,)
Shape of PCA Accel X [0]:
590
Shape of PCA Accel X [0][0]:
(100, 3)


C:\Users\User\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:3: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  This is separate from the ipykernel package so we can avoid doing imports until


In [ ]:
# Add padding so that all trials are the same length
max_length = max([len(trial) for trial in pca_accelX])
padded_pca_accelX = []

for trial in pca_accelX:
    trial_length = len(trial)
    padding = max_length - trial_length
    padded_trial = np.pad(trial, ((0, padding), (0, 0), (0, 0)), 'constant', constant_values=0)
    padded_pca_accelX.append(padded_trial)

# Save and load data

In [ ]:
# Save the data to pickle
import pickle

with open('padded_pca_accelX.pickle', 'wb') as f:
    pickle.dump(padded_pca_accelX, f)

with open('accelAbnormalY.pickle', 'wb') as f:
    pickle.dump(accelAbnormalY, f)

with open('accelAimsY.pickle', 'wb') as f:
    pickle.dump(accelAimsY, f)

with open('accelOptimalityY.pickle', 'wb') as f:
    pickle.dump(accelOptimalityY, f)

In [ ]:
# Load the data from pickle
with open('padded_pca_accelX.pickle', 'rb') as f:
    padded_pca_accelX = pickle.load(f)

with open('accelAbnormalY.pickle', 'rb') as f:
    accelAbnormalY = pickle.load(f)

with open('accelAimsY.pickle', 'rb') as f:
    accelAimsY = pickle.load(f)

with open('accelOptimalityY.pickle', 'rb') as f:
    accelOptimalityY = pickle.load(f)

In [ ]:
# Create test and train set
from sklearn.model_selection import train_test_split

# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(padded_pca_accelX, accelAbnormalY, test_size=0.2, random_state=42)

# Sanity check: Print results
print("X_train:")
print(len(X_train))

X_train:
128


In [ ]:
print(X_train[0].shape)

(1842, 100, 3)


In [ ]:
import numpy as np

X_train = np.array(X_train)
X_train = X_train.reshape((X_train.shape[0], 1842, 100, 3))

X_test = np.array(X_test)
X_test = X_test.reshape((X_test.shape[0], 1842, 100, 3))


In [3]:
# Use a CNN to classify the data
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Conv2D, Flatten, MaxPooling2D, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import binary_crossentropy
from tensorflow.keras.metrics import binary_accuracy
import numpy as np

# Create the model
model = Sequential()
model.add(Conv2D(64, 3, activation='relu', input_shape=(1842, 100, 3)))
model.add(MaxPooling2D())
model.add(Conv2D(64, 3, activation='relu'))
model.add(MaxPooling2D())
model.add(Flatten())
model.add(Dense(64, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.0001), loss=binary_crossentropy, metrics=[binary_accuracy])

# Train the model
model.fit(X_train, (y_train), epochs=10, batch_size=32, validation_data=(X_test, y_test))

# Evaluate the model
loss, accuracy = model.evaluate(np.array(X_test), np.array(y_test))

# Print the accuracy
print("Accuracy:", accuracy)



NameError: name 'X_train' is not defined

In [36]:
# 10-fold random split (149/12) cross-validation. That is, every fold contains 12 trials as test

# Feed data into CNN
# Define the model

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Conv1D, Flatten, MaxPooling1D, Dropout

# Define the model
model = Sequential()
model.add(Conv1D(filters=64, kernel_size=3, activation='relu', input_shape=(100, 3)))
model.add(MaxPooling1D(pool_size=2))
model.add(Dropout(0.5))
model.add(Flatten())
model.add(Dense(100, activation='relu'))
model.add(Dense(1, activation='sigmoid'))

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Train the model
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10)

# Evaluate the model
loss, accuracy = model.evaluate(X_test, y_test)
print('Accuracy: %.2f' % (accuracy*100))


ValueError: Input arrays should have the same number of samples as target arrays. Found 1842 input samples and 128 target samples.